In [1]:
from google.colab import drive
drive.mount('/content/drive')
%cd drive/MyDrive/covid_segm/

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
/content/drive/MyDrive/covid_segm


In [2]:
import torch.nn as nn
import torch
from torch.utils.data import Dataset, DataLoader, random_split
import torchvision.transforms as T

import os
from tqdm.notebook import tqdm
from PIL import Image
import json
import nibabel as nib

import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

import random
from sklearn.metrics import classification_report

In [3]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
device

'cuda'

# Directory hierarchy and json altering

In [4]:
# !mv data datab
# !mv data .
# !rmdir datab

In [5]:
# def change_json(json_file):
#     with open(json_file) as f:
#         data = json.load(f)
    
#         for d in data:
#             d['image'] = 'data/images/' + d['image'][:-3]
#             d['label'] = 'data/labels/' + d['label'][:-3]

    
#         with open('new_' + json_file, 'w') as f_:
#             json.dump(data, f_)

# change_json('training_data.json')
# change_json('testing_data.json')

In [6]:
# !cat new_training_data.json

# Load Dataset

In [7]:
class CTDataset(Dataset):
    def __init__(self, paths, transform_x, transform_y):
        self.data_list = []
        self.transform_x = transform_x
        self.transform_y = transform_y

        with open(paths) as f:
            data = json.load(f)

            for d in data:
                image = nib.load(d['image'])
                label = nib.load(d['label'])

                self.data_list.append((image, label))

    def __len__(self):
        return len(self.data_list)

    def __getitem__(self, idx):
        nii_to_torch = lambda x: torch.from_numpy(np.asarray(x.dataobj))\
            .transpose(1, 2)\
            .transpose(0, 1)\
            .type(torch.float32)

        nii_image = self.data_list[idx]
        seed = np.random.randint(0,2**32)
        np.random.seed(seed)
        torch.manual_seed(seed)
        X = self.transform_x(nii_to_torch(nii_image[0]))

        np.random.seed(seed)
        torch.manual_seed(seed)
        Y = self.transform_y(nii_to_torch(nii_image[1]))

        return X, Y

In [8]:
def one_channel_at_a_time(batch):
    x, y = map(list, zip(*batch))

    x = torch.cat(x, dim=0).unsqueeze(1)
    y = torch.cat(y, dim=0).unsqueeze(1)

    return x, y

In [9]:
def loaders(transform_x, transform_y):
    data = CTDataset('training_data.json', transform_x, transform_y)
    train_data, test_data = random_split(data, [32, 8])
    
    if device == 'cuda':
        pin_memory = True
    else:
        pin_memory = False
    
    trainloader = DataLoader(train_data, batch_size=1,
                            shuffle=True, pin_memory=pin_memory,
                            collate_fn=one_channel_at_a_time)
    testloader = DataLoader(test_data, batch_size=1,
                            shuffle=True, pin_memory=pin_memory,
                            collate_fn=one_channel_at_a_time)
    
    return trainloader, testloader

In [10]:
resize = T.Resize((128, 128))
trainloader, testloader = loaders(resize, resize)

In [11]:
mu = 0.
sigma = 0.
for x, y in trainloader:
    mu += x.mean()
    sigma += x.std()

mu /= len(trainloader.dataset)
sigma /= len(trainloader.dataset)
standardize = T.Normalize(mean=mu, std=sigma)
standardize

Normalize(mean=-779.8301391601562, std=787.2334594726562)

In [12]:
resize = T.Resize((128, 128))
transform_x = T.Compose([resize, standardize])
trainloader, testloader = loaders(transform_x, resize)

# Train & Eval

In [13]:
def to_numpy_image(img):
    return img.detach().cpu().view(128, 128).transpose(0, 1).numpy()

In [14]:
def vis(model, loader):
    model.eval()
    with torch.no_grad():
        for x, y in loader:
            inds = torch.randint(0, x.shape[0], size=(10,))
            x = x[inds].to(device)
            y = y[inds].to(device)
    
    
            last_layer = nn.Sequential(nn.BatchNorm2d(1), nn.Sigmoid()).to(device)
            pred = last_layer(model(x)).round()

            fig = make_subplots(rows=3, cols=3)

            for i in range(1, 4):
                fig.add_trace(
                    go.Heatmap(z=to_numpy_image(x[i]), colorscale="Cividis"),
                    row=i, col=1
                )
                fig.add_trace(
                    go.Heatmap(z=to_numpy_image(pred[i]), colorscale="Cividis"),
                    row=i, col=2
                )
                fig.add_trace(
                    go.Heatmap(z=to_numpy_image(y[i]), colorscale="Cividis"),
                    row=i, col=3
                )

            fig.update_traces(showscale=False)
            fig.show(renderer='colab')
    
            break

In [15]:
def test(model, loader):
    model.eval()
    with torch.no_grad():
        y_true = []
        y_pred = []
        cnt = 0
        for x, y in loader:
            if cnt == 8:
                break
            cnt += 1
            x = x.to(device)
            y = y.to(device)

            last_layer = nn.Sequential(nn.BatchNorm2d(1), nn.Sigmoid()).to(device)
            pred = last_layer(model(x)).round()

            y_true.extend(y.flatten().type(torch.int32).tolist())
            y_pred.extend(pred.flatten().type(torch.int32).tolist())

    rep = classification_report(y_true, y_pred, output_dict=True)
    sensitivity = rep['1']['recall']
    specificity = rep['0']['recall']
    f1_macro = rep['macro avg']['f1-score']

    return [sensitivity, specificity, f1_macro]

In [16]:
def draw_class_rep(train_metrics, test_metrics):
    train_sens = train_metrics[0]
    train_spec = train_metrics[1]
    train_f1 = train_metrics[2]
    test_sens = test_metrics[0]
    test_spec = test_metrics[1]
    test_f1 = test_metrics[2]
    fig = go.Figure()
    
    fig.add_trace(go.Scatter(
        y=train_sens,
        x=np.arange(len(train_sens)),
        name="Train sensitivity"       # this sets its legend entry
    ))
    fig.add_trace(go.Scatter(
        y=train_sens,
        x=np.arange(len(test_sens)),
        name="Test sensitivity"       # this sets its legend entry
    ))
    fig.update_layout(
        title="Sensitivity",
        xaxis_title="Epoch",
        yaxis_title="Score",
    )
    fig.show()
    fig = go.Figure()
    fig.add_trace(go.Scatter(
        y=train_spec,
        x=np.arange(len(train_spec)),
        name="Train pecificity"
    ))
    fig.add_trace(go.Scatter(
        y=test_spec,
        x=np.arange(len(test_spec)),
        name="Test specificity"
    ))
    fig.update_layout(
        title="Specificity",
        xaxis_title="Epoch",
        yaxis_title="Score",
    )   
    fig.show()

    fig = go.Figure()
    fig.add_trace(go.Scatter(
        y=train_f1,
        x=np.arange(len(train_f1)),
        name="Train F1-Score"
    ))
    fig.add_trace(go.Scatter(
        y=test_f1,
        x=np.arange(len(test_f1)),
        name="Test F1-Score"
    ))
    
    fig.update_layout(
        title="F1-Score",
        xaxis_title="Epoch",
        yaxis_title="Score",
    )
    fig.show()

In [17]:
def save(path, epoch, model, optimizer, history, train_metrics, test_metrics):
    torch.save({
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'loss': history,
            'train_metrics': train_metrics,
            'test_metrics': test_metrics
            }, path)

In [18]:
def train(model, criterion, optimizer, trainloader, testloader, name, epochs=20):
    history = []
    train_metrics = []
    test_metrics = []

    for epoch in range(epochs):
        model.train()
        for x, y in tqdm(trainloader):
            x = x.to(device)
            y = y.to(device)
            optimizer.zero_grad(set_to_none=True)

            pred = model.forward(x)
            loss = criterion(pred.flatten(start_dim=1), y.flatten(start_dim=1))

            history.append(loss.item())

            loss.backward()
            optimizer.step()

        print("epoch: %s, loss: %.4f" % (epoch + 1, history[-1]))
        if epoch != 0 and epoch % 10 == 0:
            vis(model, testloader)
            save(name, epoch, model, optimizer, history, train_metrics, test_metrics)

        train_metrics.append(test(model, trainloader))
        test_metrics.append(test(model, testloader))

    fig = px.line(history, title='train loss')
    fig.show(renderer='colab')

    train_metrics = np.array(train_metrics).T
    test_metrics = np.array(test_metrics).T
    draw_class_rep(train_metrics, test_metrics)
    print("Average sensitivity: %.6f, specificity: %.6f, f1-score: %.6f." \
          % (test_metrics[0].mean(), test_metrics[1].mean(), test_metrics[2].mean())) 

In [19]:
def calc_pos_weight(trainloader):
    pos_weight = 0.
    cnt = 0.
    for _, y in trainloader:
        pos_weight += y.sum()
        cnt += y.numel()

    pos_weight = (cnt - pos_weight) / pos_weight
    pos_weight = torch.full((128 * 128, ), pos_weight, device=device)

    return pos_weight

# Baseline

In [20]:
def Block(channels_in, channels_out, norm=True, p=0.5):
    l = [
       nn.Dropout(p=p)
    ]
    if norm:
        l += [nn.Conv2d(channels_in, channels_out, (3, 3), padding=1, bias=False),
              nn.BatchNorm2d(channels_out)]
    else:
        l += [nn.Conv2d(channels_in, channels_out, (3, 3), padding=1)]
    l += [nn.LeakyReLU(), 
         ]

    return nn.Sequential(*l)

class Shape(nn.Module):
    def __init__(self, num):
        super().__init__()
        self.num = num

    def forward(self, x):
        print(self.num, ": ", x.shape)
        return x

In [21]:
class BaselineUnet(nn.Module):
    def __init__(self):
        super().__init__()

        self.down1 = nn.Sequential(
            Block(1, 64, p=0.2),
            Block(64, 64),
            # Shape(1),
            )
        self.down2 = nn.Sequential(
            nn.MaxPool2d((2, 2), (2, 2)),
            Block(64, 128),
            Block(128, 128),
            # Shape(2),
            )
        self.down3 = nn.Sequential(
            nn.MaxPool2d((2, 2), (2, 2)),
            Block(128, 256),
            Block(256, 256),
            # Shape(3),
            )
        # self.down4 = nn.Sequential(
        #     nn.MaxPool2d((2, 2), (2, 2)),
        #     Block(256, 512),
        #     Block(512, 512),
        #     Shape(4),
        #     )
        self.right = nn.Sequential(
            nn.MaxPool2d((2, 2), (2, 2)),
            Block(256, 256),
            Block(256, 256),
            # Shape(5),
            nn.Upsample(scale_factor=2),
            Block(256, 256),
            # Shape(6),
            )
        # self.up1 = nn.Sequential(
        #     Shape(7),
        #     Block(1024, 512),
        #     Block(512, 512),
        #     nn.Upsample(scale_factor=2),
        #     Block(512, 256),
        #     Shape(8),
        # )
        self.up2 = nn.Sequential(
            # Shape(9),
            Block(512, 256),
            Block(256, 256),
            nn.Upsample(scale_factor=2),
            Block(256, 128),
            # Shape(10),
        )
        self.up3 = nn.Sequential(
            # Shape(11),
            Block(256, 128, norm=False),
            Block(128, 128, norm=False),
            nn.Upsample(scale_factor=2),
            Block(128, 64),
            # Shape(12),
        )

        self.up4 = nn.Sequential(
            # Shape(13),
            Block(128, 64, norm=False),
            Block(64, 64, norm=False),
        )

        self.final = nn.Sequential(
            # Shape(14),
            nn.Conv2d(64, 32, (3, 3), padding=1),
            nn.Conv2d(32, 8, (3, 3), padding=1),
            nn.Conv2d(8, 1, (3, 3), padding=1),
        )

    def forward(self, x):
        t1 = self.down1(x)
        t2 = self.down2(t1)
        t3 = self.down3(t2)
        # t4 = self.down4(t3)

        out = self.right(t3)

        # out = self.up1(torch.cat((t4, out), dim=1))
        out = self.up2(torch.cat((t3, out), dim=1))
        out = self.up3(torch.cat((t2, out), dim=1))
        out = self.final(self.up4(torch.cat((t1, out), dim=1)))

        return out


In [27]:
model = BaselineUnet().to(device)
criterion = nn.BCEWithLogitsLoss(pos_weight=calc_pos_weight(trainloader))
optimizer = torch.optim.Adam(model.parameters(), 1e-4)

def init_weights(m):
    if isinstance(m, nn.Conv2d):
        nn.init.kaiming_normal_(m.weight, a=0.01, nonlinearity='leaky_relu')
        if m.bias is not None:
            m.bias.data.fill_(0)

model.apply(init_weights)

train(model, criterion, optimizer, trainloader, testloader, epochs=50)

  0%|          | 0/32 [00:00<?, ?it/s]

epoch: 1, loss: 1.3136


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMe

  0%|          | 0/32 [00:00<?, ?it/s]

epoch: 2, loss: 0.9457


...

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



  0%|          | 0/32 [00:00<?, ?it/s]

epoch: 50, loss: 0.3169


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



Average sensitivity: 0.224082, specificity: 0.512502, f1-score: 0.080049.


# Augmentation

In [22]:
class AdoptForCT(nn.Module):
    def __init__(self, transform):
        super().__init__()
        self.transform = transform

    def forward(self, x):
        res = []
        for x_i in x:
            res.append(self.transform(x_i.unsqueeze(0)))

        return torch.cat(res, dim=0)

In [23]:
transform_common = T.Compose([
    T.RandomResizedCrop((128, 128)),
    T.RandomHorizontalFlip(),
    T.RandomVerticalFlip(),
    T.RandomRotation(180),
    AdoptForCT(T.GaussianBlur(3, sigma=(0.05, 1.0))),
])

transform_x = T.Compose([
    transform_common,
    standardize,
])
transform_y = T.Compose([
    transform_common,
])

trainloader, testloader = loaders(transform_x, transform_y)

In [25]:
model = BaselineUnet().to(device)
criterion = nn.BCEWithLogitsLoss(pos_weight=calc_pos_weight(trainloader))
optimizer = torch.optim.Adam(model.parameters(), 1e-4)

def init_weights(m):
    if isinstance(m, nn.Conv2d):
        nn.init.kaiming_normal_(m.weight, a=0.01, nonlinearity='leaky_relu')
        if m.bias is not None:
            m.bias.data.fill_(0)

model.apply(init_weights)

train(model, criterion, optimizer, trainloader, testloader, name='augm_model.pt', epochs=250)

  0%|          | 0/32 [00:00<?, ?it/s]

epoch: 1, loss: 1.1438


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMe

  0%|          | 0/32 [00:00<?, ?it/s]

epoch: 2, loss: 0.4166


...

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



  0%|          | 0/32 [00:00<?, ?it/s]

epoch: 12, loss: 0.5000


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning:

Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.



KeyboardInterrupt: ignored